In [82]:
import sys
import os
import string
import math
import pandas as pd
import numpy as np
import datetime
from random import *
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn import svm
from sklearn import neural_network
from sklearn import ensemble
from sklearn import gaussian_process
from sklearn import neighbors
from sklearn import naive_bayes
from sklearn import linear_model
from sklearn.preprocessing import LabelEncoder
from sklearn.feature_extraction import DictVectorizer
from sklearn import metrics
from sklearn.metrics import roc_curve, auc
from sklearn.datasets.samples_generator import make_blobs
from sklearn.feature_extraction.text import TfidfVectorizer
import matplotlib.pyplot as plt
%matplotlib inline
import pandas_profiling

In [2]:
df = pd.read_csv('final.csv')

In [3]:
df.head()

Unnamed: 0  Unnamed: 0.1    Bug ID    Product Component    Status  \
0           0             0  406140.0  Efxclipse   Runtime  RESOLVED   
1           1             1  407438.0  Efxclipse   Runtime  RESOLVED   
2           2             2  407476.0  Efxclipse   Runtime  RESOLVED   
3           3             3  408120.0  Efxclipse   Runtime  RESOLVED   
4           4             4  408286.0  Efxclipse   Tooling  RESOLVED   

  Resolution                                            Summary  \
0      FIXED  [e4] ToolItems with type check should be rende...   
1      FIXED  [e4] ThemeManager fails if no theme configured...   
2      FIXED  [EMF-Edit] AdapterFactoryObservableList does n...   
3      FIXED  [Kepler] Compiler errors introduced from generics   
4      FIXED  [PDE] OSGi Application Wizard should not disab...   

               Changed         Assignee  ...               Opened         OS  \
0  2013-04-20 04:16:37  efxclipse-inbox  ...  2013-04-20 04:01:47   Mac OS X   
1  2013-05-07 12:09:51  efxclipse-inbox  ...  2013-05-07 12:03:53   Mac OS X   
2  2013-05-07 20:00:27  efxclipse-inbox  ...  2013-05-07 19:57:40   Mac OS X   
3  2013-05-16 05:14:17      tom.schindl  ...  2013-05-15 08:35:25  Windows 7   
4  2013-05-16 17:42:17      tom.schindl  ...  2013-05-16 17:16:13   Mac OS X   

  Personal Tags Priority     Reporter     Severity  Target Milestone  \
0           NaN       P3  tom.schindl  enhancement             0.9.0   
1           NaN       P3  tom.schindl       normal             0.9.0   
2           NaN       P3  tom.schindl       normal             0.9.0   
3           NaN       P3        scela       normal             0.9.0   
4           NaN       P3  tom.schindl  enhancement             0.9.0   

       Version Votes        Activity  
0  unspecified   0.0  NEW-->RESOLVED  
1  unspecified   0.0  NEW-->RESOLVED  
2  unspecified   0.0  NEW-->RESOLVED  
3        0.8.1   0.0  NEW-->RESOLVED  
4        0.9.0   0.0  NEW-->RESOLVED  

[5 rows x 27 columns]

In [4]:
translation_table = str.maketrans(string.punctuation+'ABCDEFGHIJKLMNOPQRSTUVWXYZ',
                                     " "*len(string.punctuation)+'abcdefghijklmnopqrstuvwxyz')


def get_words_from_text(text):
    text = str(text)
    text = text.translate(translation_table)
    word_list = text.split()
    return word_list

def count_frequency(word_list):
    """
    Return a dictionary mapping words to frequency.
    """
    D = {}
    for new_word in word_list:
        if new_word in D:
            D[new_word] = D[new_word]+1
        else:
            D[new_word] = 1
    return D

def word_frequencies_for_text(text):
    """
    Return dictionary of (word,frequency) pairs for the given file.
    """
    word_list = get_words_from_text(text)
    freq_mapping = count_frequency(word_list)
    return freq_mapping

def inner_product(D1,D2):
    """
    Inner product between two vectors, where vectors
    are represented as dictionaries of (word,freq) pairs.
    Example: inner_product({"and":3,"of":2,"the":5},
                           {"and":4,"in":1,"of":1,"this":2}) = 14.0 
    """
    sum = 0.0
    for key in D1:
        if key in D2:
            sum += D1[key] * D2[key]
    return sum

def vector_angle(D1,D2):
    """
    The input is a list of (word,freq) pairs, sorted alphabetically.
    Return the angle between these two vectors.
    """
    numerator = inner_product(D1,D2)
    denominator = math.sqrt(inner_product(D1,D1)*inner_product(D2,D2))
    try:  
        return (numerator/denominator)
    except:
        return 0
        pass

In [5]:
df.head()

Unnamed: 0  Unnamed: 0.1    Bug ID    Product Component    Status  \
0           0             0  406140.0  Efxclipse   Runtime  RESOLVED   
1           1             1  407438.0  Efxclipse   Runtime  RESOLVED   
2           2             2  407476.0  Efxclipse   Runtime  RESOLVED   
3           3             3  408120.0  Efxclipse   Runtime  RESOLVED   
4           4             4  408286.0  Efxclipse   Tooling  RESOLVED   

  Resolution                                            Summary  \
0      FIXED  [e4] ToolItems with type check should be rende...   
1      FIXED  [e4] ThemeManager fails if no theme configured...   
2      FIXED  [EMF-Edit] AdapterFactoryObservableList does n...   
3      FIXED  [Kepler] Compiler errors introduced from generics   
4      FIXED  [PDE] OSGi Application Wizard should not disab...   

               Changed         Assignee  ...               Opened         OS  \
0  2013-04-20 04:16:37  efxclipse-inbox  ...  2013-04-20 04:01:47   Mac OS X   
1  2013-05-07 12:09:51  efxclipse-inbox  ...  2013-05-07 12:03:53   Mac OS X   
2  2013-05-07 20:00:27  efxclipse-inbox  ...  2013-05-07 19:57:40   Mac OS X   
3  2013-05-16 05:14:17      tom.schindl  ...  2013-05-15 08:35:25  Windows 7   
4  2013-05-16 17:42:17      tom.schindl  ...  2013-05-16 17:16:13   Mac OS X   

  Personal Tags Priority     Reporter     Severity  Target Milestone  \
0           NaN       P3  tom.schindl  enhancement             0.9.0   
1           NaN       P3  tom.schindl       normal             0.9.0   
2           NaN       P3  tom.schindl       normal             0.9.0   
3           NaN       P3        scela       normal             0.9.0   
4           NaN       P3  tom.schindl  enhancement             0.9.0   

       Version Votes        Activity  
0  unspecified   0.0  NEW-->RESOLVED  
1  unspecified   0.0  NEW-->RESOLVED  
2  unspecified   0.0  NEW-->RESOLVED  
3        0.8.1   0.0  NEW-->RESOLVED  
4        0.9.0   0.0  NEW-->RESOLVED  

[5 rows x 27 columns]

In [6]:
df = df.drop(['Unnamed: 0','Unnamed: 0.1','Bug ID','Changed','Assignee','Opened','Depends on','Personal Tags','Reporter','Flags','Hardware','Keywords','Last Visit','Number of Comments'],axis=1)

In [8]:
df = df.drop(['Target Milestone','Version','Votes'],axis=1)

In [9]:
df.head()

Product Component    Status Resolution  \
0  Efxclipse   Runtime  RESOLVED      FIXED   
1  Efxclipse   Runtime  RESOLVED      FIXED   
2  Efxclipse   Runtime  RESOLVED      FIXED   
3  Efxclipse   Runtime  RESOLVED      FIXED   
4  Efxclipse   Tooling  RESOLVED      FIXED   

                                             Summary Classification  \
0  [e4] ToolItems with type check should be rende...     Technology   
1  [e4] ThemeManager fails if no theme configured...     Technology   
2  [EMF-Edit] AdapterFactoryObservableList does n...     Technology   
3  [Kepler] Compiler errors introduced from generics     Technology   
4  [PDE] OSGi Application Wizard should not disab...     Technology   

          OS Priority     Severity        Activity  
0   Mac OS X       P3  enhancement  NEW-->RESOLVED  
1   Mac OS X       P3       normal  NEW-->RESOLVED  
2   Mac OS X       P3       normal  NEW-->RESOLVED  
3  Windows 7       P3       normal  NEW-->RESOLVED  
4   Mac OS X       P3  enhancement  NEW-->RESOLVED

In [16]:
replace_dict_Priority = {'Priority':{'P1':1,'P2':2,'P3':3,'P4':4,'P5':5}}

In [17]:
df_rep = df.copy()

In [18]:
df_rep.replace(replace_dict_Priority, inplace=True)

In [19]:
df = df_rep.copy()

In [20]:
df.head()

Product Component    Status Resolution  \
0  Efxclipse   Runtime  RESOLVED      FIXED   
1  Efxclipse   Runtime  RESOLVED      FIXED   
2  Efxclipse   Runtime  RESOLVED      FIXED   
3  Efxclipse   Runtime  RESOLVED      FIXED   
4  Efxclipse   Tooling  RESOLVED      FIXED   

                                             Summary Classification  \
0  [e4] ToolItems with type check should be rende...     Technology   
1  [e4] ThemeManager fails if no theme configured...     Technology   
2  [EMF-Edit] AdapterFactoryObservableList does n...     Technology   
3  [Kepler] Compiler errors introduced from generics     Technology   
4  [PDE] OSGi Application Wizard should not disab...     Technology   

          OS  Priority     Severity        Activity  unconfirmed  
0   Mac OS X         3  enhancement  NEW-->RESOLVED          0.0  
1   Mac OS X         3       normal  NEW-->RESOLVED          0.0  
2   Mac OS X         3       normal  NEW-->RESOLVED          0.0  
3  Windows 7         3       normal  NEW-->RESOLVED          0.0  
4   Mac OS X         3  enhancement  NEW-->RESOLVED          0.0

In [10]:
lt = []
count =0
k = df.copy()
k = k.isna()
for i in range(877833):
    if k['Activity'][i]:
        df['Activity'][i] = 'UNCONFIRMED'
        count = count + 1
print(count)        

374372


In [11]:
df.head()

Product Component    Status Resolution  \
0  Efxclipse   Runtime  RESOLVED      FIXED   
1  Efxclipse   Runtime  RESOLVED      FIXED   
2  Efxclipse   Runtime  RESOLVED      FIXED   
3  Efxclipse   Runtime  RESOLVED      FIXED   
4  Efxclipse   Tooling  RESOLVED      FIXED   

                                             Summary Classification  \
0  [e4] ToolItems with type check should be rende...     Technology   
1  [e4] ThemeManager fails if no theme configured...     Technology   
2  [EMF-Edit] AdapterFactoryObservableList does n...     Technology   
3  [Kepler] Compiler errors introduced from generics     Technology   
4  [PDE] OSGi Application Wizard should not disab...     Technology   

          OS Priority     Severity        Activity  
0   Mac OS X       P3  enhancement  NEW-->RESOLVED  
1   Mac OS X       P3       normal  NEW-->RESOLVED  
2   Mac OS X       P3       normal  NEW-->RESOLVED  
3  Windows 7       P3       normal  NEW-->RESOLVED  
4   Mac OS X       P3  enhancement  NEW-->RESOLVED

In [12]:
for k in range(len(df)):
    i = df['Activity'][k]
    if (i.find('UNCONFIRMED') != -1 and (i.find('RESOLVED') == -1 and i.find('CLOSED') == -1)):
        df.at[k,'unconfirmed'] = 1
        print(i)
    else:
        df.at[k,'unconfirmed'] = 0

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED-->NEW
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED-->NEW
UNCO

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

...

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCONFIRMED
UNCO

In [59]:
df.head()

Product Component    Status Resolution  \
0  Efxclipse   Runtime  RESOLVED      FIXED   
1  Efxclipse   Runtime  RESOLVED      FIXED   
2  Efxclipse   Runtime  RESOLVED      FIXED   
3  Efxclipse   Runtime  RESOLVED      FIXED   
4  Efxclipse   Tooling  RESOLVED      FIXED   

                                             Summary Classification  \
0  [e4] ToolItems with type check should be rende...     Technology   
1  [e4] ThemeManager fails if no theme configured...     Technology   
2  [EMF-Edit] AdapterFactoryObservableList does n...     Technology   
3  [Kepler] Compiler errors introduced from generics     Technology   
4  [PDE] OSGi Application Wizard should not disab...     Technology   

          OS  Priority     Severity        Activity  unconfirmed  reopened  \
0   Mac OS X         3  enhancement  NEW-->RESOLVED          0.0       0.0   
1   Mac OS X         3       normal  NEW-->RESOLVED          0.0       0.0   
2   Mac OS X         3       normal  NEW-->RESOLVED          0.0       0.0   
3  Windows 7         3       normal  NEW-->RESOLVED          0.0       0.0   
4   Mac OS X         3  enhancement  NEW-->RESOLVED          0.0       0.0   

   fix accepted  
0           1.0  
1           1.0  
2           1.0  
3           1.0  
4           1.0

In [72]:
sm = 0
lt = []
for i in range(len(df)):
    if df['unconfirmed'][i] or df['reopened'][i] or df['fix accepted'][i]:
        sm = sm + 1
    else:
        lt.append([df['Activity'][i],df['Resolution'][i]])
print(sm) 

805401


In [81]:
lm = []
for i in range(len(lt)):
    if lt[i][0] == 'CLOSED' or lt[i][0] == 'VERIFIED' or lt[i][0] == 'RESOLVED':
        lm.append(lt[i][1])
print(set(lm))    

{'INVALID'}


In [32]:
count = 0
for k in range(len(df)):
    i = str(df['Activity'][k])
    if (i.find('REOPENED') != -1):
        count = count + 1
        df.at[k,'reopened'] = 1
    else:
        df.at[k,'reopened'] = 0

In [45]:
count = 0
for k in range(len(df)):
    i = str(df['Resolution'][k])
    #print(i)
    if(i == 'WONTFIX' or i == 'WORKSFORME'):
        count = count + 1
        df.at[k,'unconfirmed'] = 1
print(count)        

69362


In [57]:
count = 0
lt = []
for k in range(len(df)):
    i = str(df['Activity'][k])
    if (df['Resolution'][k] == 'DUPLICATE' or df['Resolution'][k] == 'FIXED'):
        df.at[k,'fix accepted'] = 1
    else:
        df.at[k,'fix accepted'] = 0


In [71]:
count = 0
for k in range(len(df)):
    i = str(df['Activity'][k])
    i = i.split('-->')
    if i == 'CLOSED' or i == 'VERIFIED' or i == 'RESOLVED'

CLOSED


In [83]:
df.head()

Product Component    Status Resolution  \
0  Efxclipse   Runtime  RESOLVED      FIXED   
1  Efxclipse   Runtime  RESOLVED      FIXED   
2  Efxclipse   Runtime  RESOLVED      FIXED   
3  Efxclipse   Runtime  RESOLVED      FIXED   
4  Efxclipse   Tooling  RESOLVED      FIXED   

                                             Summary Classification  \
0  [e4] ToolItems with type check should be rende...     Technology   
1  [e4] ThemeManager fails if no theme configured...     Technology   
2  [EMF-Edit] AdapterFactoryObservableList does n...     Technology   
3  [Kepler] Compiler errors introduced from generics     Technology   
4  [PDE] OSGi Application Wizard should not disab...     Technology   

          OS  Priority     Severity        Activity  unconfirmed  reopened  \
0   Mac OS X         3  enhancement  NEW-->RESOLVED          0.0       0.0   
1   Mac OS X         3       normal  NEW-->RESOLVED          0.0       0.0   
2   Mac OS X         3       normal  NEW-->RESOLVED          0.0       0.0   
3  Windows 7         3       normal  NEW-->RESOLVED          0.0       0.0   
4   Mac OS X         3  enhancement  NEW-->RESOLVED          0.0       0.0   

   fix accepted  
0           1.0  
1           1.0  
2           1.0  
3           1.0  
4           1.0

In [88]:
labeler = LabelEncoder()
for i in ['Product','Component','Status','Resolution','Classification','OS','Severity']:
    st = i + ' Code'
    df[st] = labeler.fit_transform(df[i])

In [94]:
df = df.drop(['Status Code','Resolution Code'], axis= 1)

In [95]:
df.to_csv('ready_for_training.csv')

In [91]:
df

Product Component    Status Resolution  \
0        Efxclipse   Runtime  RESOLVED      FIXED   
1        Efxclipse   Runtime  RESOLVED      FIXED   
2        Efxclipse   Runtime  RESOLVED      FIXED   
3        Efxclipse   Runtime  RESOLVED      FIXED   
4        Efxclipse   Tooling  RESOLVED      FIXED   
5        Efxclipse   Tooling  RESOLVED      FIXED   
6        Efxclipse   Tooling  RESOLVED      FIXED   
7        Efxclipse   Tooling  RESOLVED      FIXED   
8        Efxclipse   Tooling  RESOLVED      FIXED   
9        Efxclipse   Runtime  RESOLVED      FIXED   
10       Efxclipse   Runtime  RESOLVED      FIXED   
11       Efxclipse   Runtime  RESOLVED      FIXED   
12       Efxclipse   Runtime  RESOLVED      FIXED   
13       Efxclipse   Runtime  RESOLVED      FIXED   
14       Efxclipse   Tooling  RESOLVED      FIXED   
15       Efxclipse   Tooling  RESOLVED      FIXED   
16       Efxclipse   Tooling  RESOLVED      FIXED   
17       Efxclipse   Tooling  RESOLVED      FIXED   
18       Efxclipse   Runtime  RESOLVED      FIXED   
19       Efxclipse   Runtime  RESOLVED      FIXED   
20       Efxclipse   Runtime  RESOLVED      FIXED   
21       Efxclipse   Tooling  RESOLVED      FIXED   
22       Efxclipse   Runtime  RESOLVED      FIXED   
23       Efxclipse   Tooling  RESOLVED      FIXED   
24       Efxclipse   Tooling  RESOLVED      FIXED   
25       Efxclipse   Tooling  RESOLVED      FIXED   
26       Efxclipse   Tooling  RESOLVED      FIXED   
27       Efxclipse   Runtime  RESOLVED      FIXED   
28       Efxclipse   Tooling  RESOLVED      FIXED   
29       Efxclipse   Tooling  RESOLVED      FIXED   
...            ...       ...       ...        ...   
877803  EMFCompare      Core       NEW        ---   
877804  EMFCompare      Core       NEW        ---   
877805  EMFCompare      Core       NEW        ---   
877806  EMFCompare      Core       NEW        ---   
877807  EMFCompare        UI       NEW        ---   
877808  EMFCompare        UI       NEW        ---   
877809  EMFCompare      Core       NEW        ---   
877810  EMFCompare        UI       NEW        ---   
877811  EMFCompare      Core       NEW        ---   
877812  EMFCompare        UI       NEW        ---   
877813  EMFCompare        UI       NEW        ---   
877814  EMFCompare      Core       NEW        ---   
877815  EMFCompare        UI       NEW        ---   
877816  EMFCompare      Core       NEW        ---   
877817  EMFCompare      Core       NEW        ---   
877818  EMFCompare        UI       NEW        ---   
877819  EMFCompare      Team       NEW        ---   
877820  EMFCompare      Team       NEW        ---   
877821  EMFCompare        UI       NEW        ---   
877822  EMFCompare        UI       NEW        ---   
877823  EMFCompare   Diagram       NEW        ---   
877824  EMFCompare      Team       NEW        ---   
877825  EMFCompare        UI       NEW        ---   
877826  EMFCompare        UI       NEW        ---   
877827  EMFCompare        UI       NEW        ---   
877828  EMFCompare      Core       NEW        ---   
877829  EMFCompare      Core       NEW        ---   
877830  EMFCompare      Team       NEW        ---   
877831  EMFCompare      Core       NEW        ---   
877832  EMFCompare        UI       NEW        ---   

                                                  Summary Classification  \
0       [e4] ToolItems with type check should be rende...     Technology   
1       [e4] ThemeManager fails if no theme configured...     Technology   
2       [EMF-Edit] AdapterFactoryObservableList does n...     Technology   
3       [Kepler] Compiler errors introduced from generics     Technology   
4       [PDE] OSGi Application Wizard should not disab...     Technology   
5       [PDE] OSGi Application Wizard generates $windo...     Technology   
6       [JDK8] Add JavaDoc location for jfxrt.jar libr...     Technology   
7                          Refactoring leads to exception     Technology   
8       built ant script doesn't handle 